
# Predicting the Dow Jones with News

## General Data flow for a Text Related Business Problem

![title](resources/textmining.png)

# Problem Statement & Reference Architecture

* **Aim**: Use Reddit News Headlines to predict the movement of Dow Jones Industrial Average.   


* **Data Source**: https://www.kaggle.com/aaron7sun/stocknews 


* **Data Description**: Dow Jones details on Open, High, Low and Close for each day from 2008-08-08 to 2016-07-01 and headlines for those dates from Reddit News. 


* **Methodology**: For this project, we will use GloVe to create our word embeddings and CNNs followed by LSTMs to build our model. This model is based off the work done in this paper https://www.aclweb.org/anthology/C/C16/C16-1229.pdf.

![basic](resources/basic_intent.png)

# Installation Prerequisites

In [1]:
!apt-get update  && apt-get install -y --allow-downgrades --no-install-recommends git wget 


Ign:1 http://developer.download.nvidia.com/compute/cuda/repos/ubuntu1704/x86_64  InRelease
Hit:2 http://archive.canonical.com/ubuntu bionic InRelease                     
Hit:3 http://security.ubuntu.com/ubuntu bionic-security InRelease   
Hit:4 http://asia-east1.gce.archive.ubuntu.com/ubuntu bionic InRelease   
Hit:5 http://developer.download.nvidia.com/compute/cuda/repos/ubuntu1704/x86_64  Release
Hit:7 http://asia-east1.gce.archive.ubuntu.com/ubuntu bionic-updates InRelease
Hit:8 http://asia-east1.gce.archive.ubuntu.com/ubuntu bionic-backports InRelease
Reading package lists... Done
E: Could not get lock /var/lib/dpkg/lock-frontend - open (11: Resource temporarily unavailable)
E: Unable to acquire the dpkg frontend lock (/var/lib/dpkg/lock-frontend), is another process using it?


In [2]:
!apt-get -y install graphviz

E: Could not get lock /var/lib/dpkg/lock-frontend - open (11: Resource temporarily unavailable)
E: Unable to acquire the dpkg frontend lock (/var/lib/dpkg/lock-frontend), is another process using it?


In [3]:
!pip install nltk keras

You are using pip version 19.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [4]:
!pip install pydot

You are using pip version 19.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [5]:
!pip install graphviz

You are using pip version 19.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [6]:
!wget http://nlp.stanford.edu/data/glove.840B.300d.zip

--2020-03-13 06:25:35--  http://nlp.stanford.edu/data/glove.840B.300d.zip
Connecting to 10.150.0.3:3128... connected.
Proxy request sent, awaiting response... 302 Found
Location: https://nlp.stanford.edu/data/glove.840B.300d.zip [following]
--2020-03-13 06:25:36--  https://nlp.stanford.edu/data/glove.840B.300d.zip
Connecting to 10.150.0.3:3128... connected.
Proxy request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/glove.840B.300d.zip [following]
--2020-03-13 06:25:37--  http://downloads.cs.stanford.edu/nlp/data/glove.840B.300d.zip
Reusing existing connection to 10.150.0.3:3128.
Proxy request sent, awaiting response... 200 OK
Length: 2176768927 (2.0G) [application/zip]
Saving to: ‘glove.840B.300d.zip’

glove.840B.300d.zip 100%[===================>]   2.03G  2.06MB/s    in 16m 58s 

2020-03-13 06:42:35 (2.04 MB/s) - ‘glove.840B.300d.zip’ saved [2176768927/2176768927]



In [11]:
!unzip glove.840B.300d.zip

SyntaxError: invalid syntax (<ipython-input-11-04a77c49309d>, line 1)

# Imports

In [12]:
import pandas as pd
import numpy as np
import tensorflow as tf
import re
import nltk
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
from sklearn.metrics import median_absolute_error as mae
from sklearn.metrics import mean_squared_error as mse
import matplotlib.pyplot as plt

In [13]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [14]:
# Keras Imports
from keras.models import Sequential
from keras import initializers
from keras.layers import Dropout, Activation, Embedding, Convolution1D, MaxPooling1D, Input, Dense, add, \
                         BatchNormalization, Flatten, Reshape, Concatenate
from keras.layers.recurrent import LSTM, GRU
from keras.callbacks import Callback, ModelCheckpoint, EarlyStopping, ReduceLROnPlateau
from keras.models import Model
from keras.optimizers import Adam, SGD, RMSprop
from keras import regularizers
from keras.utils.vis_utils import plot_model
import re

Using TensorFlow backend.


In [15]:
dj = pd.read_csv("dowjones-news-data/DowJones.csv")
news = pd.read_csv("dowjones-news-data/News.csv")

## Inspect the data

In [16]:
dj.head()

Date          Open          High           Low         Close  \
0  2016-07-01  17924.240234  18002.380859  17916.910156  17949.369141   
1  2016-06-30  17712.759766  17930.609375  17711.800781  17929.990234   
2  2016-06-29  17456.019531  17704.509766  17456.019531  17694.679688   
3  2016-06-28  17190.509766  17409.720703  17190.509766  17409.720703   
4  2016-06-27  17355.210938  17355.210938  17063.080078  17140.240234   

      Volume     Adj Close  
0   82160000  17949.369141  
1  133030000  17929.990234  
2  106380000  17694.679688  
3  112190000  17409.720703  
4  138740000  17140.240234

In [17]:
dj.isnull().sum() #No missing data

Date         0
Open         0
High         0
Low          0
Close        0
Volume       0
Adj Close    0
dtype: int64

In [18]:
news.isnull().sum() #No missing data

Date    0
News    0
dtype: int64

In [19]:
news.head()

Date                                               News
0  2016-07-01  A 117-year-old woman in Mexico City finally re...
1  2016-07-01   IMF chief backs Athens as permanent Olympic host
2  2016-07-01  The president of France says if Brexit won, so...
3  2016-07-01  British Man Who Must Give Police 24 Hours' Not...
4  2016-07-01  100+ Nobel laureates urge Greenpeace to stop o...

In [20]:
print(dj.shape)
print(news.shape)

(1989, 7)
(73608, 2)


In [21]:
# Compare the number of unique dates. We want matching values.
print(len(set(dj.Date)))
print(len(set(news.Date)))

1989
2943


In [22]:
# Remove the extra dates that are in news
news = news[news.Date.isin(dj.Date)]

In [23]:
print(len(set(dj.Date)))
print(len(set(news.Date)))

1989
1989


In [24]:
# Remove unwanted features - keep the 'Open' price only
dj = dj.drop(['High','Low','Close','Volume','Adj Close'], 1)
dj.head()

Date          Open
0  2016-07-01  17924.240234
1  2016-06-30  17712.759766
2  2016-06-29  17456.019531
3  2016-06-28  17190.509766
4  2016-06-27  17355.210938

In [25]:
# Calculate the difference in opening prices between the following and current day.
# The model will try to predict the change in Open value based on the today's news.
dj = dj.set_index('Date')
dj.head()

Open
Date                    
2016-07-01  17924.240234
2016-06-30  17712.759766
2016-06-29  17456.019531
2016-06-28  17190.509766
2016-06-27  17355.210938

In [26]:
# Target variable = Tomorrow's Open Price - Today's Open Price
dj = -1 * dj.diff(periods=1)

In [27]:
dj.head()

Open
Date                  
2016-07-01         NaN
2016-06-30  211.480468
2016-06-29  256.740235
2016-06-28  265.509765
2016-06-27 -164.701172

In [28]:
dj['Date'] = dj.index
dj = dj.reset_index(drop=True)

In [29]:
dj.head()

Open        Date
0         NaN  2016-07-01
1  211.480468  2016-06-30
2  256.740235  2016-06-29
3  265.509765  2016-06-28
4 -164.701172  2016-06-27

In [30]:
# Remove top row since it has a null value.
dj = dj[dj.Open.notnull()]

In [31]:
# Check if there are any more null values.
dj.isnull().sum()

Open    0
Date    0
dtype: int64

## Combine the two datasets - For each date, get all the headlines and the price

In [32]:
# Create a list of the opening prices and their corresponding daily headlines from the news
# Define/Initialize the variables
price = []
headlines = []

# For all the rows in the dataframe
for row in dj.iterrows():
    # define a new variable to store all the headlines for the day
    daily_headlines = []
    # Spot the date in the given row
    date = row[1]['Date']
    # Store the price for the date
    price.append(row[1]['Open'])
    for row_ in news[news.Date==date].iterrows():
        daily_headlines.append(row_[1]['News'])

    # Append the headlines for the date
    headlines.append(daily_headlines)
    # Track progress
    if len(price) % 500 == 0:
        print(len(price))

500
1000
1500


<table size="100">
    <tr>
        <td>headlines</td>
        <td>price</td>
    </tr>
    <tr>
        <td>headline-1, headline-2 ..., headline-n</td>
        <td>211.48</td>
    </tr>
</table>

In [33]:
# Check how headlines look like
headlines[:1], price[:1]

([['Jamaica proposes marijuana dispensers for tourists at airports following legalisation: The kiosks and desks would give people a license to purchase up to 2 ounces of the drug to use during their stay',
   "Stephen Hawking says pollution and 'stupidity' still biggest threats to mankind: we have certainly not become less greedy or less stupid in our treatment of the environment over the past decade",
   'Boris Johnson says he will not run for Tory party leadership',
   'Six gay men in Ivory Coast were abused and forced to flee their homes after they were pictured signing a condolence book for victims of the recent attack on a gay nightclub in Florida',
   'Switzerland denies citizenship to Muslim immigrant girls who refused to swim with boys: report',
   'Palestinian terrorist stabs israeli teen girl to death in her bedroom',
   'Puerto Rico will default on $1 billion of debt on Friday',
   'Republic of Ireland fans to be awarded medal for sportsmanship by Paris mayor.',
   "Afghan s

## Clean up the price list

In [34]:
price[:2]

[211.48046800000157, 256.7402349999975]

In [35]:
# Normalize opening prices (target values)
max_price = max(price)
min_price = min(price)
mean_price = np.mean(price)
def normalize(price):
    return ((price-min_price)/(max_price-min_price))

In [36]:
norm_price = []
for p in price:
    norm_price.append(normalize(p))

In [37]:
# Check that normalization worked well
print(min(norm_price))
print(max(norm_price))
print(np.mean(norm_price))

0.0
1.0
0.4551577545098642


In [38]:
# Compare the number of headlines for each day
print(max(len(i) for i in headlines))
print(min(len(i) for i in headlines))
print(np.mean([len(i) for i in headlines]))

25
22
24.996478873239436


In [39]:
norm_price[:2]

[0.5780280759194737, 0.6047364662478155]

## Clean up the headlines list

In [40]:
# remove contractions
def decontracted(phrase):
    if "'" in phrase:
        # specific
        phrase = re.sub(r"won't", "will not", phrase)
        phrase = re.sub(r"can\'t", "can not", phrase)

        # general
        phrase = re.sub(r"n\'t", " not", phrase)
        phrase = re.sub(r"\'re", " are", phrase)
        phrase = re.sub(r"\'s", " is", phrase)
        phrase = re.sub(r"\'d", " would", phrase)
        phrase = re.sub(r"\'ll", " will", phrase)
        phrase = re.sub(r"\'t", " not", phrase)
        phrase = re.sub(r"\'ve", " have", phrase)
        phrase = re.sub(r"\'m", " am", phrase)
    return phrase

text = "I should've gone to dentist so my teeth wouldn't hurt"
text1 = "But I am good now"
print(decontracted(text))
print(decontracted(text1))

I should have gone to dentist so my teeth would not hurt
But I am good now


In [42]:
def clean_text(text):
    '''Remove unwanted characters and format the text to create fewer nulls word embeddings'''
    
    # Convert words to lower case
    text = text.lower()
    
    # Replace contractions with their longer forms 
    if True:
        text = text.split()
        new_text = []
        # Remove the contractions
        for word in text:
            new_text.append(decontracted(word))
        # Recreate the sentence
        text = " ".join(new_text)
    
    # Format words and remove unwanted characters
    text = re.sub(r'&amp;', '', text) 
    text = re.sub(r'0,0', '00', text) 
    text = re.sub(r'[_"\-;%()|.,+&=*%.,!?:#@\[\]]', ' ', text)
    text = re.sub(r'\'', ' ', text)
    text = re.sub(r'\$', ' $ ', text)
    text = re.sub(r'u s ', ' united states ', text)
    text = re.sub(r'u n ', ' united nations ', text)
    text = re.sub(r'u k ', ' united kingdom ', text)
    text = re.sub(r'j k ', ' jk ', text)
    text = re.sub(r' s ', ' ', text)
    text = re.sub(r' yr ', ' year ', text)
    text = re.sub(r' l g b t ', ' lgbt ', text)
    text = re.sub(r'0km ', '0 km ', text)
    
    # Remove stop words
    text = text.split()
    stops = set(stopwords.words("english"))
    text = [w for w in text if not w in stops]
    text = " ".join(text)

    return text

In [43]:
# Clean the headlines
clean_headlines = []

for daily_headlines in headlines:
    clean_daily_headlines = []
    for headline in daily_headlines:
        clean_daily_headlines.append(clean_text(headline))
    clean_headlines.append(clean_daily_headlines)

In [44]:
# Take a look at some headlines to ensure everything was cleaned well
clean_headlines[:2]

[['jamaica proposes marijuana dispensers tourists airports following legalisation kiosks desks would give people license purchase 2 ounces drug use stay',
  'stephen hawking says pollution istupidity still biggest threats mankind certainly become less greedy less stupid treatment environment past decade',
  'boris johnson says run tory party leadership',
  'six gay men ivory coast abused forced flee homes pictured signing condolence book victims recent attack gay nightclub florida',
  'switzerland denies citizenship muslim immigrant girls refused swim boys report',
  'palestinian terrorist stabs israeli teen girl death bedroom',
  'puerto rico default $ 1 billion debt friday',
  'republic ireland fans awarded medal sportsmanship paris mayor',
  'afghan suicide bomber kills 40 bbc news',
  'us airstrikes kill least 250 isis fighters convoy outside fallujah official says',
  'turkish cop took istanbul gunman hailed hero',
  'cannabis compounds could treat alzheimer removing plaque formin

In [45]:
print('Roughly the number of unique words in English: {}'.format(len({word: None 
                                                                      for headlines in clean_headlines 
                                                                      for headline in headlines 
                                                                      for word in headline.split()})))


Roughly the number of unique words in English: 36311


In [47]:
x={word: None 
                                                                      for headlines in clean_headlines 
                                                                      for headline in headlines 
                                                                      for word in headline.split()}

In [50]:
# Create the word vocab
import collections
words = [word for headlines in clean_headlines for headline in headlines for word in headline.split()]
word_counts = collections.Counter(words)

In [51]:
word_counts

Counter({'jamaica': 23,
         'proposes': 65,
         'marijuana': 216,
         'dispensers': 1,
         'tourists': 95,
         'airports': 33,
         'following': 219,
         'legalisation': 4,
         'kiosks': 2,
         'desks': 1,
         'would': 888,
         'give': 289,
         'people': 1887,
         'license': 21,
         'purchase': 26,
         '2': 733,
         'ounces': 2,
         'drug': 648,
         'use': 605,
         'stay': 107,
         'stephen': 59,
         'hawking': 23,
         'says': 2563,
         'pollution': 135,
         'istupidity': 2,
         'still': 326,
         'biggest': 331,
         'threats': 118,
         'mankind': 13,
         'certainly': 12,
         'become': 314,
         'less': 204,
         'greedy': 6,
         'stupid': 27,
         'treatment': 133,
         'environment': 96,
         'past': 242,
         'decade': 109,
         'boris': 23,
         'johnson': 24,
         'run': 291,
         'tory': 24

# A note on Word Embeddings

![word_embed](resources/wordvectors.png)

**Reference**: https://nlp.stanford.edu/projects/glove/

## We are going to use Glove embeddings to initialize our weights while designing our neural network. Let's load the same so that we can ensure our headline corpus' vocabulary matches where possible with Glove Embedding vocabulary.

In [52]:
# Load GloVe's embeddings
embeddings_index = {}
with open('glove.840B.300d.txt', encoding='utf-8') as f:
    for line in f:
        values = line.split(' ')
        word = values[0]
        embedding = np.asarray(values[1:], dtype='float32')
        embeddings_index[word] = embedding

print('Word embeddings:', len(embeddings_index))

Word embeddings: 2196016


## It is not necessary that we will have embeddings for all the words in Glove. So to limit such cases by limiting vocabulary by applying simple logic:  Remove the words that are "rare" and are not available in Glove 

In [53]:
# Limit the vocab that we will use to words that appear ≥ threshold or are in GloVe

# Define threshold
threshold = 10

#dictionary to convert words to integers
vocab_to_int = {} 

value = 0
for word, count in word_counts.items():
    if count >= threshold or word in embeddings_index:
        vocab_to_int[word] = value
        value += 1

In [55]:
vocab_to_int

{'jamaica': 0,
 'proposes': 1,
 'marijuana': 2,
 'dispensers': 3,
 'tourists': 4,
 'airports': 5,
 'following': 6,
 'legalisation': 7,
 'kiosks': 8,
 'desks': 9,
 'would': 10,
 'give': 11,
 'people': 12,
 'license': 13,
 'purchase': 14,
 '2': 15,
 'ounces': 16,
 'drug': 17,
 'use': 18,
 'stay': 19,
 'stephen': 20,
 'hawking': 21,
 'says': 22,
 'pollution': 23,
 'still': 24,
 'biggest': 25,
 'threats': 26,
 'mankind': 27,
 'certainly': 28,
 'become': 29,
 'less': 30,
 'greedy': 31,
 'stupid': 32,
 'treatment': 33,
 'environment': 34,
 'past': 35,
 'decade': 36,
 'boris': 37,
 'johnson': 38,
 'run': 39,
 'tory': 40,
 'party': 41,
 'leadership': 42,
 'six': 43,
 'gay': 44,
 'men': 45,
 'ivory': 46,
 'coast': 47,
 'abused': 48,
 'forced': 49,
 'flee': 50,
 'homes': 51,
 'pictured': 52,
 'signing': 53,
 'condolence': 54,
 'book': 55,
 'victims': 56,
 'recent': 57,
 'attack': 58,
 'nightclub': 59,
 'florida': 60,
 'switzerland': 61,
 'denies': 62,
 'citizenship': 63,
 'muslim': 64,
 'immigra

In [54]:
len(vocab_to_int)

31295

In [56]:
# Special tokens that will be added to our vocab
codes = ["<UNK>","<PAD>"]   

# Add codes to vocab
for code in codes:
    vocab_to_int[code] = len(vocab_to_int)

# Dictionary to convert integers to words
int_to_vocab = {}
for word, value in vocab_to_int.items():
    int_to_vocab[value] = word

usage_ratio = round(len(vocab_to_int) / len(word_counts),4)*100

print("Total Number of Unique Words:", len(word_counts))
print("Number of Words we will use:", len(vocab_to_int))
print("Percent of Words we will use: {}%".format(usage_ratio))

Total Number of Unique Words: 36311
Number of Words we will use: 31297
Percent of Words we will use: 86.19%


## For the words which are common within headlines but are absent in Glove corpus, we will have to randomly initialize them. Over the training, those values will be finetuned along with those of Glove vectors.

In [57]:
# Need to use 300 for embedding dimensions to match GloVe's vectors.
embedding_dim = 300

nb_words = len(vocab_to_int)
# Create matrix with default values of zero
word_embedding_matrix = np.zeros((nb_words, embedding_dim))
for word, i in vocab_to_int.items():
    if word in embeddings_index:
        word_embedding_matrix[i] = embeddings_index[word]
    else:
        # If word not in GloVe, create a random embedding for it
        new_embedding = np.array(np.random.uniform(-1.0, 1.0, embedding_dim))
        embeddings_index[word] = new_embedding
        word_embedding_matrix[i] = new_embedding

# Check if value matches len(vocab_to_int)
print(len(word_embedding_matrix))

31297


## Convert the word sequences to equivalent integer sequences so that it can be used as input to the model

In [58]:
# Change the text from words to integers
# If word is not in vocab, replace it with <UNK> (unknown)
word_count = 0
unk_count = 0

headlines_sequence = []

for daily_headline in clean_headlines:
    daily_headlines_seq = []
    for headline in daily_headline:
        headline_seq = []
        for word in headline.split():
            word_count += 1
            if word in vocab_to_int:
                headline_seq.append(vocab_to_int[word])
            else:
                headline_seq.append(vocab_to_int["<UNK>"])
                unk_count += 1
        daily_headlines_seq.append(headline_seq)
    headlines_sequence.append(daily_headlines_seq)

unk_percent = round(unk_count/word_count,4)*100

print("Total number of words in headlines:", word_count)
print("Total number of UNKs in headlines:", unk_count)
print("Percent of words that are UNK: {}%".format(unk_percent))

Total number of words in headlines: 616686
Total number of UNKs in headlines: 7139
Percent of words that are UNK: 1.16%


In [105]:
len(headlines_sequence)
type(headlines_sequence[0][0][0])

int

In [98]:
len(headlines_sequence[0:1][0][2])

7

In [112]:
a=headlines_sequence[:1]
for k in range(len(headlines_sequence)):
    for i in range(len(headlines_sequence[k])) :
        print(headlines_sequence[k][i], end="\n")
        #for j in range(len(headlines_sequence[k][i])) :  
        #    print(headlines_sequence[k][i], end="\n") 
    print("================") 

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19]
[20, 21, 22, 23, 31295, 24, 25, 26, 27, 28, 29, 30, 31, 30, 32, 33, 34, 35, 36]
[37, 38, 22, 39, 40, 41, 42]
[43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 44, 59, 60]
[61, 62, 63, 64, 65, 66, 67, 68, 69, 70]
[71, 72, 73, 74, 75, 76, 77, 78]
[79, 80, 81, 82, 83, 84, 85, 86]
[87, 88, 89, 90, 91, 92, 93, 94]
[95, 96, 97, 98, 99, 100, 101]
[102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 22]
[113, 114, 115, 116, 117, 118, 119]
[120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132]
[133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 102, 72, 143, 144, 145, 146, 22, 147, 64, 148, 149]
[150, 151, 152, 153, 154, 155, 156]
[157, 158, 159, 160, 161, 162, 163, 164, 165]
[166, 167, 168, 169, 170, 171, 172, 173, 174, 175]
[176, 177, 132, 178, 179, 180, 181, 182, 183, 184, 185]
[45, 186, 187, 188, 58, 116, 189, 190, 191, 192, 193, 113, 194, 195]
[196, 161, 162, 163, 197, 198, 164, 165, 199, 200

[303, 3813, 155, 4468, 3580, 605, 6807, 6808, 637, 3518, 1024, 3496, 2050, 939, 6809, 6810, 6811, 6812, 122, 3842, 929, 3893, 6813, 4573, 6814]
[6815, 3726, 3756, 500, 107, 477, 1930, 184]
[807, 4183, 951, 3536, 874, 2314, 159, 1555]
[6816, 6817, 1576, 2106, 1387, 6816, 6818, 2290, 384, 6819, 6820, 1658, 2106, 260, 2200, 6133]
[1605, 932, 1270, 102, 1417, 820, 300, 1645, 5395, 3150, 637, 2297, 4049, 4302, 413, 627, 1784, 2638, 6821, 1322, 579, 580]
[786, 2299, 358, 955, 6822, 214, 687, 184, 1163, 6823, 1128, 150]
[910, 911, 4341, 6824, 4680, 354, 355, 305, 2060, 416]
[5671, 2908, 6825, 1825, 1826, 578, 77, 260, 188, 647, 77, 2908, 382, 437, 276, 4626, 239, 679]
[6826, 745, 6827, 2130, 665, 300, 681, 1325, 34, 2147, 22, 6828, 6829, 122, 6830, 579, 754, 3506, 4318]
[3433, 5282, 437, 276, 6831, 6832, 1436, 6833, 677]
[6834, 3568, 2482, 5465, 520, 437, 1552]
[162, 6835, 1127, 628, 3300, 202, 25, 6836, 102]
[102, 6837, 1257, 6838, 3765, 3656, 3791]
[303, 2534, 177, 6839, 308, 6840, 983, 548

[835, 2177, 64, 2194, 1035, 187, 6596, 9251, 9732, 9733, 437, 1350, 2194, 396, 876, 523, 1488, 139, 6596, 1699, 5555, 369, 7061, 9734, 9735, 9736, 9737, 2876, 1873]
[1593, 807, 5144, 9168, 4170, 4668, 808, 5757]
[1706, 1516, 872, 31295, 9738, 6, 805, 1735, 807, 808]
[2055, 7578, 1831, 4283, 22, 807, 6072, 1706, 31295, 9739, 2355, 287, 3683, 3684, 2160, 326, 9740, 8798, 1552, 195, 2412, 3000, 139, 9741, 822, 5909, 2025, 1045, 195]
[191, 566, 3557, 1185, 2314]
[155, 3113, 212, 64, 341, 5045, 1217, 560, 415, 416, 5974]
[102, 1496, 1387, 2292, 1490]
[3021, 30, 1399, 2335, 504, 2141, 872, 309, 5236, 5806, 2111, 4665, 2306, 309, 310, 2679, 1400, 9742, 310]
[1134, 196, 9359, 2077, 805, 9743, 807, 808]
[1785, 3801, 9744, 3005, 936, 6078, 1769]
[9745, 9746, 4573, 5992, 3327, 2474, 9137, 2291, 310, 31295, 9747, 9748, 864, 9749]
[437, 243, 58, 264, 93, 989, 4223, 1593, 9750, 9751, 738, 1900]
[3002, 1633, 6834, 9752, 260, 7531, 315]
[800, 3122, 107, 6333, 88, 22, 134, 64, 2317]
[9753, 462, 102, 68

[113, 2040, 4837, 1186, 514, 735, 619, 1348, 549, 600, 1348]
[4792, 5185, 8107, 2298, 2278, 3910, 437, 703, 4485, 2335]
[3999, 358, 11423, 324, 2791, 4535]
[776, 894, 2848, 913, 2552, 2777, 3609, 8200, 12059, 237, 2335, 3865, 7873, 469, 142, 3557, 3213, 1683, 12060, 8050, 4902, 776, 10851, 1654, 12061, 4901, 776, 444, 12062, 11074, 12063, 1224, 2552]
[169, 12064, 503, 120, 12065, 681, 396, 1043]
[611, 9997, 351, 4485, 122, 8280, 4792]
[191, 1730, 83, 354, 4183, 2096, 657, 1436, 697, 5000, 8927, 907, 2232, 1436, 870, 1187, 1799, 1436, 1628, 12066, 499, 9617, 3295, 3294, 1482, 2465, 1116]
[2931, 1554, 1164, 1547, 331, 453, 814, 22]
[4121, 3147, 12067, 12068, 3177, 2066, 294, 1766, 2455, 9666, 5831, 4060, 3295, 207, 12069, 17]
[991, 6676, 2064, 102, 10983, 211, 2610, 7039, 991, 1602, 558, 792, 159, 1555, 3472, 610, 199, 309, 310, 4797, 2460, 1645, 615, 3511, 3233, 746, 1871, 977, 989]
[311, 2299, 483, 22, 7956, 2611, 12070, 3140, 115, 522, 155, 482, 70, 4432, 12071]
[711, 4815, 22, 393, 1

[2199, 14256, 1073, 116, 4013, 2259]
[71, 11861, 1508, 415, 5560, 3736, 14257, 58, 71, 4223, 7111, 287, 10467, 7045, 2922, 6996, 3330, 3691, 4025, 14258, 162, 702, 230, 201]
[14259, 1310, 14260, 13693, 3845, 14181, 4473, 676, 183, 4370]
[287, 536, 3849, 1485, 1035, 2033, 694, 1117, 10, 2558, 453, 2060, 104, 2662, 1073, 2259]
[6379, 1322, 31295, 3973, 1658, 551, 3974]
[442, 1378, 2180, 511, 1091, 9893, 1502]
[2256, 3510, 1268, 637, 3823, 14261, 1159, 43, 315, 1955, 2175, 164, 627, 2559, 336, 548, 858, 3823, 14262, 611, 980, 2256, 3510, 4746, 14263, 7747]
[864, 135, 8273, 64, 3728, 184, 1233, 13535, 238, 4356, 477, 15, 184, 3544, 4735]
[12706, 249, 1802, 3615, 3616, 3347, 354, 355, 3002, 6280, 4431, 4281, 2544, 5412, 5413]
[1417, 1082, 1082, 5544, 3284, 2481, 437, 2482, 1314, 3447, 1339]
[3614, 2366, 77, 1874, 1300, 14264, 2143, 4186, 3799, 8274, 470, 3343, 58]
[5215, 201, 1588, 3697, 2374, 2421, 1683, 105, 1638]
[4869, 22, 102, 103, 142, 107, 8787, 22, 107, 162, 163, 8999, 14265]
[162, 

...

[5967, 3433, 9061, 9964, 249, 4955, 1331, 3917, 418, 494, 954, 9991, 2767, 538, 6483, 1236, 3188, 5435]
[5967, 1839, 1127, 2992, 11994, 264, 1554, 2766, 2355, 800, 26874, 8923]
[5967, 15744, 8111, 28475, 7239, 7664, 249, 12888, 2767, 2782, 28387, 77, 13141, 681, 1838, 26978, 393, 520, 416, 2722, 109, 1118, 8130, 10687]
[5967, 12304, 28925, 31295, 201, 1350, 326, 22, 1233, 1453, 2734, 201, 1157, 3139, 11312, 139, 1628, 2583, 2584, 13535]
[5967, 7968, 101, 28926, 28927, 1907, 1070, 2304, 1028, 28926, 28927]
[5967, 10413, 1879, 1582, 437, 2937, 439, 31295, 3953]
[5967, 991, 211, 25, 437, 438, 301]
[5967, 1554, 9129, 10065, 31295, 438, 1170]
[5967, 11392, 977, 85, 2112, 1741, 12, 2140, 24, 2112, 1880, 3571, 249, 58, 12]
[5967, 7075, 354, 355, 212, 1585, 6151, 3858, 2331, 249, 1155, 1879, 1269, 222, 24252]
[5967, 31295, 580, 2698, 1017, 4141]
[5967, 5236, 1332, 28710, 28928, 24019, 88, 12999, 3508, 260, 405, 8484, 354, 355, 4356, 3509, 7579, 2930, 354, 355, 9116]
[5967, 569, 4109, 6749, 800

[5967, 294, 800, 22, 1345, 2303, 10153, 4277, 294, 684, 11409, 1594, 269, 2694, 372, 7578]
[5967, 7842, 415, 2277, 13663, 2268, 1194, 140, 21059, 4424, 3487, 18250, 2111, 7940, 2335, 140, 295, 9030, 3768, 9678]
[5967, 3523, 97, 4395, 4961]
[5967, 4719, 3178, 843, 5357, 3555, 5197, 3839, 294, 10190, 6694, 5357, 165, 5717, 6617]
[5967, 9953, 341, 5332, 2537, 91, 20036, 2331, 1073, 2361, 3924, 927, 211, 6617, 6214]
[5967, 31295, 10293, 1839, 3433, 6857, 3859]
[5967, 2464, 835, 11694, 2064, 105, 2464, 61, 11694, 8553]
[5967, 294, 2534, 82, 7397, 199, 13559]
[5967, 462, 3247, 342, 29731, 2347, 18586, 3408, 31295, 9671, 291, 31295, 2347, 6, 5099]
[5967, 1554, 3642, 14787, 746, 11154, 1164, 1306]
[5967, 14031, 2158, 150, 766]
[5967, 583, 9731, 3677, 10649, 1831, 453, 6803, 13812, 1161, 2541, 3871, 31295, 3723, 633, 1832, 3658, 7127, 2406, 351]
[5967, 83, 1426, 864, 224, 2773, 29732, 1629, 1935, 3666]
[5967, 12292, 349, 3836, 15046, 1581, 2700, 287, 22, 13812, 4283, 2656, 82, 314, 84, 1820]
[5

[5967, 1236, 11666, 358, 7279, 47]
[5967, 30345, 2141, 31295, 30346, 975, 642, 10476, 1119, 83, 2245, 2474, 9664]
[5967, 30347, 14592, 3252, 4202, 3968]
[5967, 355, 1002, 4775, 974, 14226, 3757, 746, 340]
[5967, 19408, 4760, 4761, 1587]
[5967, 31295, 90, 11325, 15534]
[5967, 4719, 2205, 2712, 30348]
[5967, 579, 2545, 3985, 17965, 31295, 6789, 631, 579, 2545, 2727]
[5967, 1702, 7186, 4449, 6824, 212, 249, 9764, 9893, 1281, 10057, 17654]
[5967, 212, 249, 2424, 31295, 459]
[5967, 74, 287, 503, 211, 614, 1164, 1382, 5303, 4378, 1382, 1350, 30098, 1946, 30349, 7032, 1683]
[5967, 31295, 1325, 2205, 41]
[5967, 1618, 416, 1802, 1626, 6135, 2165, 2169]
[5967, 437, 4431, 1784, 249, 9519, 1109, 1061, 2069, 12, 20994, 8959, 4431]
[5967, 991, 229, 2233, 1421, 514, 9763, 3502, 4074, 596, 5196]
[5967, 2355, 5138, 618, 44, 45, 30350, 16396]
[5967, 31295, 4329, 6024, 10830, 6926, 520, 27331, 5675, 30351, 3395, 2606, 5602, 17549, 482, 5983]
[5967, 13570, 1971, 11326, 2745]
[5967, 1691, 22843, 6862, 1106

[5967, 1097, 6501, 8737, 2863, 1554, 287, 10467, 13451]
[5967, 31295, 15546, 260, 261, 8737, 112, 6151, 1831]
[5967, 31295, 8737, 927, 1694]
[5967, 469, 2066, 6250, 15397]
[5967, 11817, 30766, 10314, 1322, 147, 10617, 30767, 3599, 39, 3237, 736, 31295, 17689, 4817, 1987, 7300, 6308]
[5967, 226, 2506, 31295, 16355]
[5967, 31295, 471, 437, 4170, 6853, 4716]
[5967, 669, 4173, 20596, 1483]
[5967, 31295, 4573, 549, 2863]
[5967, 31295, 286, 30768, 416, 30769, 4398, 1829, 2185, 25321, 1120, 4918, 96, 1628, 3140, 1170, 5133, 1585, 2485, 24857]
[5967, 31295, 22599, 4147, 10078]
[5967, 4931, 3394, 3691, 6987]
[5967, 453, 1105, 15767]
[5967, 2482, 4164, 1502, 9757, 10487]
[5967, 14650, 10721, 28193, 1508, 281, 1767, 4256, 30770, 211, 295, 1948, 1767]
[5967, 1105, 2473, 449, 6662, 1108, 1105, 453, 499]
[5967, 31295, 1701, 77, 26, 843, 762, 30771, 22285]
[5967, 1767, 6502, 2008, 1508, 31295]
[5967, 745, 9657, 477, 82, 2076, 1973, 84, 1300, 548, 477, 82, 2076, 3728, 84, 3813, 477, 82, 83, 15, 84, 70

[5967, 415, 72, 3396, 1895]
[5967, 294, 217, 4549, 4744, 280, 6014, 1785, 12]
[5967, 11252, 22, 1602, 984, 807, 1357, 1298, 3172, 13603, 159, 1555, 229, 595, 1357, 9086, 715, 5804, 87]
[5967, 31248, 437, 55, 35, 999, 1579, 1085, 6088, 3542, 3550, 5553, 29, 5039, 2901, 522, 160, 2454]
[5967, 5729, 1942, 191, 10, 2424, 1353, 537, 14390, 3722, 19067, 3049, 58, 903, 2611, 405, 1304]
[5967, 31295, 326, 1226, 7680, 7124, 7125]
[5967, 27953, 812, 1831, 453, 30523, 482, 7127]
[5967, 191, 31249, 3757, 437, 211, 9478]
[5967, 2351, 1028, 9583, 31295, 1879, 1774, 991, 18764, 9743, 1198, 859, 157]
[5967, 5713, 981, 11243, 5368, 67, 294, 2147, 1871, 3408, 544, 4357, 261]
[5967, 12936, 1657, 2059, 2055, 2056, 29, 1420, 676, 870, 1540, 1657]
[5967, 311, 6258, 8829, 633]
[5967, 212, 800, 1375, 3085, 324, 151, 159, 1555]
[5967, 28608, 2177, 2355, 7694, 2998, 1219, 8301, 439, 4103, 13306, 7519, 2169]
[5967, 21052, 864, 1279, 2421]
[5967, 10984, 1954, 16705, 3239, 5153, 10, 951, 336, 5729, 8352, 4263]
[59

## Ensure that the variations in the number of news headlines each day and length of each headlines are handled by taking an average number of headlines each day and average length per headline 

In [113]:
# Find the length of headlines
lengths = []
for headlines in headlines_sequence:
    for headline in headlines:
        lengths.append(len(headline))

# Create a dataframe so that the values can be inspected
lengths = pd.DataFrame(lengths, columns=['counts'])

In [114]:
lengths.describe()

counts
count  49693.000000
mean      12.409917
std        6.789827
min        1.000000
25%        7.000000
50%       10.000000
75%       16.000000
max       41.000000

## Limit the length of a day's news to 200 words, and the length of any headline to 16 words. These values are chosen to not have an excessively long training time and balance the number of headlines used and the number of words from each headline.

In [116]:
max_headline_length = 16
max_daily_length = 200
pad_headlines = []

# For each date in all the dates available
for headlines in headlines_sequence:
    pad_daily_headlines = []
    # for each headline for each date
    for headline in headlines:
        # Add headline if it is less than max length
        if len(headline) <= max_headline_length:
            for word in headline:
                pad_daily_headlines.append(word)
        # Limit headline if it is more than max length  
        else:
            headline = headline[:max_headline_length]
            for word in headline:
                pad_daily_headlines.append(word)
    
    # Pad daily_headlines if they are less than max length
    if len(pad_daily_headlines) < max_daily_length:
        for i in range(max_daily_length-len(pad_daily_headlines)):
            pad = vocab_to_int["<PAD>"]
            pad_daily_headlines.append(pad)
    # Limit daily_headlines if they are more than max length
    else:
        pad_daily_headlines = pad_daily_headlines[:max_daily_length]
    pad_headlines.append(pad_daily_headlines)

## Split data into training and testing sets.
## Validating data will be created during training.

In [117]:
x_train, x_test, y_train, y_test = train_test_split(pad_headlines, norm_price, test_size = 0.15, random_state = 2)

x_train = np.array(x_train)
x_test = np.array(x_test)
y_train = np.array(y_train)
y_test = np.array(y_test)

In [118]:
# Check the lengths
print(len(x_train))
print(len(x_test))

1689
299


# Model Building

## The CNN-RNN architecture
![cnn-rnn](resources/cnn-1d-rnn.jpg)

## 1. Define the hyperparameters

In [119]:
filter_length = 5
dropout = 0.5
learning_rate = 0.001
weights = initializers.TruncatedNormal(mean=0.0, stddev=0.1, seed=2)
nb_filter = 16
rnn_output_size = 128
hidden_dims = 128

## 2. Create the model

In [120]:
def build_model():
    
    model = Sequential()
    
    # Layer 1 - Embedding
    model.add(Embedding(nb_words, 
                         embedding_dim,
                         weights=[word_embedding_matrix], 
                         input_length=max_daily_length))
    model.add(Dropout(dropout))
    
    # Layer 2 - Convolution 1 with dropout
    model.add(Convolution1D(filters = nb_filter, 
                             kernel_size = filter_length, 
                             padding = 'same',
                             activation = 'relu'))
    model.add(Dropout(dropout))    

    # Layer 3 - Convolution 2 with Dropout 
    model.add(Convolution1D(filters = nb_filter, 
                                 kernel_size = filter_length, 
                                 padding = 'same',
                                 activation = 'relu'))
    model.add(Dropout(dropout))    

    # Layer 4 - RNN with dropout
    model.add(LSTM(rnn_output_size, 
                    activation=None,
                    kernel_initializer=weights,
                    dropout = dropout))    

    # Layer 5 - Dense FFN with Dropout
    model.add(Dense(hidden_dims, kernel_initializer=weights))
    model.add(Dropout(dropout))
    
    model.add(Dense(1, 
                    kernel_initializer = weights,
                    name='output'))

    model.compile(loss='mean_squared_error',
                  optimizer=Adam(lr=learning_rate,clipvalue=1.0))
    return model

## 3. Fit the model

In [121]:
model = build_model()
print()
save_best_weights = 'best_weights.h5'

callbacks = [ModelCheckpoint(save_best_weights, monitor='val_loss', save_best_only=True),
            EarlyStopping(monitor='val_loss', patience=5, verbose=1, mode='auto'),
            ReduceLROnPlateau(monitor='val_loss', factor=0.2, verbose=1, patience=3)]

history = model.fit([x_train],
                    y_train,
                    batch_size=128,
                    epochs=100,
                    validation_split=0.15,
                    verbose=True,
                    shuffle=True,
                    callbacks = callbacks)
print(model.summary())


Train on 1435 samples, validate on 254 samples
Epoch 1/100
1435/1435 [==============================] - 21s 15ms/step - loss: 0.0832 - val_loss: 0.0677
Epoch 2/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0304 - val_loss: 0.0440
Epoch 3/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0209 - val_loss: 0.0211
Epoch 4/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0157 - val_loss: 0.0159
Epoch 5/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0132 - val_loss: 0.0106
Epoch 6/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0116 - val_loss: 0.0087
Epoch 7/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0106 - val_loss: 0.0084
Epoch 8/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0107 - val_loss: 0.0073
Epoch 9/100
1435/1435 [==============================] - 6s 4ms/step - loss: 0.0098 - val_loss: 0.0077
Epoch 10/100
1435/1435 

## 4. Predict using the model

In [122]:
predictions = model.predict([x_test], verbose = True)

299/299 [==============================] - 2s 7ms/step


In [123]:
# Compare testing loss to training and validating loss
mse(y_test, predictions)

0.007451776235339992

In [124]:
# Revert prediction back to actual scale
def unnormalize(price):
    '''Revert values to their unnormalized amounts'''
    price = price*(max_price-min_price)+min_price
    return(price)

In [125]:
# Store back-scaled predictions
unnorm_predictions = []
for pred in predictions:
    unnorm_predictions.append(unnormalize(pred))

# Store back-scaled actuals
unnorm_y_test = []
for y in y_test:
    unnorm_y_test.append(unnormalize(y))

In [126]:
# Calculate the median absolute error for the predictions
mae(unnorm_y_test, unnorm_predictions)

85.89495818359319

In [127]:
pd.Series(unnorm_y_test).describe()

count    299.000000
mean       7.094101
std      139.532324
min     -673.139648
25%      -54.689941
50%       10.759766
75%       87.465332
max      541.050782
dtype: float64

## Make Your Own Predictions

Below is the code necessary to make your own predictions. I found that the predictions are most accurate when there is no padding included in the input data. In the create_news variable, I have some default news that you can use, which is from April 30th, 2017. Just change the text to whatever you want, then see the impact your new headline will have.

In [128]:
def news_to_int(news):
    '''Convert your created news into integers'''
    ints = []
    for word in news.split():
        if word in vocab_to_int:
            ints.append(vocab_to_int[word])
        else:
            ints.append(vocab_to_int['<UNK>'])
    return ints

In [129]:
def padding_news(news):
    '''Adjusts the length of your created news to fit the model's input values.'''
    padded_news = news
    if len(padded_news) < max_daily_length:
        for i in range(max_daily_length-len(padded_news)):
            padded_news.append(vocab_to_int["<PAD>"])
    elif len(padded_news) > max_daily_length:
        padded_news = padded_news[:max_daily_length]
    return padded_news

In [130]:
# Default news that you can use

create_news =  "Woman says note from Chinese 'prisoner' was hidden in new purse. \
               21,000 AT&T workers poised for Monday strike \
               housands march against Trump climate policies in D.C., across USA \
               Kentucky judge won't hear gay adoptions because it's not in the child's \"best interest\" \
               Multiple victims shot in UTC area apartment complex \
               Drones Lead Police to Illegal Dumping in Riverside County | NBC Southern California \
               An 86-year-old Californian woman has died trying to fight a man who was allegedly sexually assaulting her 61-year-old friend. \
               Fyre Festival Named in $5Million+ Lawsuit after Stranding Festival-Goers on Island with Little Food, No Security. \
               The \"Greatest Show on Earth\" folds its tent for good \
               U.S.-led fight on ISIS have killed 352 civilians: Pentagon \
               Woman offers undercover officer sex for $25 and some Chicken McNuggets \
               Ohio bridge refuses to fall down after three implosion attempts \
               Jersey Shore MIT grad dies in prank falling from library dome \
               New York graffiti artists claim McDonald's stole work for latest burger campaign \
               SpaceX to launch secretive satellite for U.S. intelligence agency \
               Severe Storms Leave a Trail of Death and Destruction Through the U.S. \
               Hamas thanks N. Korea for its support against ‘Israeli occupation’ \
               Baker Police officer arrested for allegedly covering up details in shots fired investigation \
               Miami doctor’s call to broker during baby’s delivery leads to $33.8 million judgment \
               Minnesota man gets 15 years for shooting 5 Black Lives Matter protesters \
               South Australian woman facing possible 25 years in Colombian prison for drug trafficking \
               The Latest: Deal reached on funding government through Sept. \
               Russia flaunts Arctic expansion with new military bases"

clean_news = clean_text(create_news)

int_news = news_to_int(clean_news)

pad_news = padding_news(int_news)

pad_news = np.array(pad_news).reshape((1,-1))

pred = model.predict([pad_news])

price_change = unnormalize(pred)

print("The Dow should open: {} from the previous open.".format(np.round(price_change[0][0],2)))

The Dow should open: -37.959999084472656 from the previous open.
